In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

비보호좌회전, 신호우회전, 유턴

줄임말 목록
- `i` : 교차로번호, `inter_no`
- `f` : 진입, from, `inc_edge_id`
- `t` : 진출, to, `out_edge_id`
- `vec` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `dire` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `rvec` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `inter2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `inter2incs` : `inter_no` $\mapsto$ `inc_edge_ids`
- `inter2outs` : `inter_no` $\mapsto$ `out_edge_ids`
- `inter2inc2dire` : `inter_no` $\mapsto$ `int2dire`
  - `inc2dire` : `out_edge_id` $\mapsto$ `dire`
- `inter2out2dire` : `inter_no` $\mapsto$ `out2dire`
  - `out2dire` : `inc_edge_id` $\mapsto$ `dire`
- `inter2inc2vec` : `inter_no` $\mapsto$ `int2vec`
  - `inc2vec` : `out_edge_id` $\mapsto$ `vec`
- `inter2out2vec` : `inter_no` $\mapsto$ `out2vec`
  - `out2vec` : `inc_edge_id` $\mapsto$ `vec`

좌회전 판단

Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.

In [2]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.u_turn = pd.merge(self.u_turn, self.u_condition, on='child_id')
display(self.u_turn)

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


parent_id child_id adj_from_edge_id adj_to_edge_id     from_edge_id  \
0        i0      u00    -571500487_01   571500487_01     571500487_02   
1        i2      u20     571542811_02   571542811_01  571542810_01.51   
2        i3      u30     571556450_02   571556450_01     571556452_01   
3        i3      u31    -571500475_01   571500475_01     571500475_02   
4        i3      u32  571540303_02.21   571540303_01     571540303_02   
5        i6      u60  571500535_02.18   571500535_01     571500535_02   

        to_edge_id condition  
0  571500487_01.32      좌회전시  
1     571542810_02     보행신호시  
2     571556452_02     보행신호시  
3  571500475_01.26     보행신호시  
4    -571540303_02     보행신호시  
5    -571500535_02      좌회전시

In [3]:
# p2inc_edge2angle : node_id to inc_edge2angle
p2inc_edge2angle = dict()
# p2out_edge2angle : node_id to out_edge2angle
p2out_edge2angle = dict()
# p2inc_angle2edge : node_id to inc_angle2edge
p2inc_angle2edge = dict()
# p2out_angle2edge : node_id to out_angle2edge
p2out_angle2edge = dict()
for node_id in self.parent_ids:
    m5 = self.match5[self.match5.node_id==node_id]
    m5 = m5.dropna(subset=['inc_edge_id', 'out_edge_id'])
    # inc_edge2angle : inc_edge_id to inc_angle
    inc_edge2angle = dict(zip(m5.inc_edge_id, m5.inc_angle.astype(int)))
    p2inc_edge2angle[node_id] = inc_edge2angle
    # out_edge2angle : out_edge_id to out_angle
    out_edge2angle = dict(zip(m5.out_edge_id, m5.out_angle.astype(int)))
    p2out_edge2angle[node_id] = out_edge2angle
    # inc_angle2edge : inc_angle to inc_edge_id
    inc_angle2edge = dict(zip(m5.inc_angle.astype(int), m5.inc_edge_id))
    p2inc_angle2edge[node_id] = inc_angle2edge
    # out_angle2edge : out_angle to out_edge_id
    out_angle2edge = dict(zip(m5.out_angle.astype(int), m5.out_edge_id))
    p2out_angle2edge[node_id] = out_angle2edge

In [4]:
self.match5

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0        175         1         A        8        남        북       179   
1        175         1         B        4        북        남       001   
2        175         2         A        7        북        동       001   
3        175         2         B        3        남        서       179   
4        175         3         A        6        동        서       090   
5        175         3         B        1        동        남       090   
6        175         4         A        5        서        북       270   
7        175         4         B        2        서        동       270   
8        176         1         A        8        남        북       180   
9        176         1         B        4        북        남       359   
10       176         2         A        8        남        북       180   
11       176         2         B        3        남        서       180   
12       176         3         A        5        서        북       270   
13       176         3         B       18      NaN      NaN       NaN   
14       177         1         A        8        남        북       179   
15       177         1         B        4        북        남       000   
16       177         2         A        7        북        동       000   
17       177         2         B        3        남        서       179   
18       177         3         A       17      NaN      NaN       NaN   
19       177         3         B       18      NaN      NaN       NaN   
20       177         4         A        5        서        북       268   
21       177         4         B        1        동        남       090   
22       178         1         A        8        남        북       180   
23       178         1         B        4        북        남       000   
24       178         2         A        7        북        동       000   
25       178         2         B        3        남        서       180   
26       178         3         A        5        서        북       270   
27       178         3         B        2        서        동       270   
28       178         4         A        6        동        서       090   
29       178         4         B        1        동        남       090   
30       201         1         A        8        남        북       180   
31       201         1         B        3        남        서       180   
32       201         2         A        5        서        북       270   
33       201         2         B        2        서        동       270   
34       201         3         A        6        동        서       090   
35       201         3         B        2        서        동       270   
36       201         4         A        6        동        서       090   
37       201         4         B        1        동        남       090   
38       201         5         A        7        북        동       000   
39       201         5         B        4        북        남       000   
40       202         1         A        6        동        서       090   
41       202         1         B        2        서        동       270   
42       202         2         A       17      NaN      NaN       NaN   
43       202         2         B       18      NaN      NaN       NaN   
44       206         1         A        8        남        북       180   
45       206         1         B        4        북        남       000   
46       206         2         A       17      NaN      NaN       NaN   
47       206         2         B       18      NaN      NaN       NaN   
48       206         3         A        8        남        북       180   
49       206         3         B        4        북        남       000   
50       206         4         A       17      NaN      NaN       NaN   
51       206         4         B       18      NaN      NaN       NaN   
52       210         1         A        6        동        서       090   
53       210         1         B       18      NaN      NaN   

In [5]:
print(self.parent_ids)

['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']


In [6]:
parent_id = self.parent_ids[1]
display(p2inc_angle2edge[parent_id])
display(p2inc_edge2angle[parent_id])

{180: '-571542810_01', 359: '571542797_02.99', 270: '571543469_02'}

{'-571542810_01': 180, '571542797_02.99': 359, '571543469_02': 270}

In [7]:
self.u_turn

parent_id child_id adj_from_edge_id adj_to_edge_id     from_edge_id  \
0        i0      u00    -571500487_01   571500487_01     571500487_02   
1        i2      u20     571542811_02   571542811_01  571542810_01.51   
2        i3      u30     571556450_02   571556450_01     571556452_01   
3        i3      u31    -571500475_01   571500475_01     571500475_02   
4        i3      u32  571540303_02.21   571540303_01     571540303_02   
5        i6      u60  571500535_02.18   571500535_01     571500535_02   

        to_edge_id condition  
0  571500487_01.32      좌회전시  
1     571542810_02     보행신호시  
2     571556452_02     보행신호시  
3  571500475_01.26     보행신호시  
4    -571540303_02     보행신호시  
5    -571500535_02      좌회전시

In [13]:
self.match1

Unnamed: 0  inter_no  phas_A  phas_B  move_A  move_B
0            0       175       1       1       8       4
1            1       175       2       2       7       3
2            2       175       3       3       6       1
3            3       175       3       4       6       2
4            4       175       4       4       5       2
5            5       176       1       1       8       4
6            6       176       2       2       8       3
7            7       176       3       3       5      18
8            8       177       1       1       8       4
9            9       177       2       2       7       3
10          10       177       3       3      17      18
11          11       177       4       4       5       1
12          12       178       1       1       8       4
13          13       178       2       2       7       3
14          14       178       3       3       5       2
15          15       178       4       4       6       1
16          16       201       1       1       8       3
17          17       201       2       2       5       2
18          18       201       3       3       6       2
19          19       201       4       4       6       1
20          20       201       5       5       7       4
21          21       202       1       1       6       2
22          22       202       2       2      17      18
23          23       206       1       1       8       4
24          24       206       2       2      17      18
25          25       206       3       3       8       4
26          26       206       4       4      17      18
27          27       210       1       1       6      18
28          28       210       1       2       6       2
29          29       210       2       2       5       2
30          30       210       3       3       7       4
31          31       210       4       4       8       3

In [12]:
self.match5

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0        175         1         A        8        남        북       179   
1        175         1         B        4        북        남       001   
2        175         2         A        7        북        동       001   
3        175         2         B        3        남        서       179   
4        175         3         A        6        동        서       090   
5        175         3         B        1        동        남       090   
6        175         4         A        5        서        북       270   
7        175         4         B        2        서        동       270   
8        176         1         A        8        남        북       180   
9        176         1         B        4        북        남       359   
10       176         2         A        8        남        북       180   
11       176         2         B        3        남        서       180   
12       176         3         A        5        서        북       270   
13       176         3         B       18      NaN      NaN       NaN   
14       177         1         A        8        남        북       179   
15       177         1         B        4        북        남       000   
16       177         2         A        7        북        동       000   
17       177         2         B        3        남        서       179   
18       177         3         A       17      NaN      NaN       NaN   
19       177         3         B       18      NaN      NaN       NaN   
20       177         4         A        5        서        북       268   
21       177         4         B        1        동        남       090   
22       178         1         A        8        남        북       180   
23       178         1         B        4        북        남       000   
24       178         2         A        7        북        동       000   
25       178         2         B        3        남        서       180   
26       178         3         A        5        서        북       270   
27       178         3         B        2        서        동       270   
28       178         4         A        6        동        서       090   
29       178         4         B        1        동        남       090   
30       201         1         A        8        남        북       180   
31       201         1         B        3        남        서       180   
32       201         2         A        5        서        북       270   
33       201         2         B        2        서        동       270   
34       201         3         A        6        동        서       090   
35       201         3         B        2        서        동       270   
36       201         4         A        6        동        서       090   
37       201         4         B        1        동        남       090   
38       201         5         A        7        북        동       000   
39       201         5         B        4        북        남       000   
40       202         1         A        6        동        서       090   
41       202         1         B        2        서        동       270   
42       202         2         A       17      NaN      NaN       NaN   
43       202         2         B       18      NaN      NaN       NaN   
44       206         1         A        8        남        북       180   
45       206         1         B        4        북        남       000   
46       206         2         A       17      NaN      NaN       NaN   
47       206         2         B       18      NaN      NaN       NaN   
48       206         3         A        8        남        북       180   
49       206         3         B        4        북        남       000   
50       206         4         A       17      NaN      NaN       NaN   
51       206         4         B       18      NaN      NaN       NaN   
52       210         1         A        6        동        서       090   
53       210         1         B       18      NaN      NaN   

In [10]:
i = 1
row = self.u_turn.iloc[i]

parent_id = row.parent_id
child_id = row.child_id
condition = row.condition
inc_edge_id = row.from_edge_id
out_edge_id = row.to_edge_id
adj_from_edge_id = row.adj_from_edge_id

# match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
cmatch = cmatch.dropna(subset=['inc_angle', 'out_angle'])
cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
cmatch['node_id'] = child_id
print(parent_id, child_id, condition)
display(cmatch)

# 헤드엣지가 포함된 행
head_true = cmatch.inc_edge_id==adj_from_edge_id

# 헤드엣지 각도
inc_angle_head = p2inc_edge2angle[parent_id][adj_from_edge_id]
print(inc_angle_head)

# 이격각도
self.angle_separation = 10

# 진입로 각도 목록
inc_angles = cmatch.inc_angle.astype(int).unique()
inc_angles = np.sort(inc_angles)
inc_angles = list(inc_angles - 360) + list(inc_angles) + list(inc_angles + 360)
inc_angles = np.array(inc_angles)
print(inc_angles)

# 보행신호시의 진입로 각도
inc_angles_left = inc_angles[inc_angles >= inc_angle_head + self.angle_separation]
inc_angle_pedes = np.sort(inc_angles_left)[0] % 360
print(inc_angles_left)
print(inc_angle_pedes)

# 보행신호시의 진입로 엣지id
inc_angle2edge = p2inc_angle2edge[parent_id]
inc_edge_id_pedes = inc_angle2edge[inc_angle_pedes]
print(inc_edge_id_pedes)

# 진출로 각도 목록
out_angles = cmatch.out_angle.astype(int).unique()
out_angles = np.sort(out_angles)
out_angles = list(out_angles - 360) + list(out_angles) + list(out_angles + 360)
out_angles = np.array(out_angles)
print(out_angles)

# 보행신호시의 진입로 각도
out_angles_right = out_angles[out_angles <= inc_angle_head - self.angle_separation]
out_angle_pedes = np.sort(out_angles_right)[-1] % 360
print(out_angles_right)

print(out_angle_pedes)

# 보행신호시의 진입로 엣지id
out_angle2edge = p2out_angle2edge[parent_id]
out_edge_id_pedes = out_angle2edge[out_angle_pedes]
print(out_edge_id_pedes)

# 보행신호시 조건
pedes_flag = (cmatch.inc_edge_id==inc_edge_id_pedes) & (cmatch.out_edge_id==out_edge_id_pedes)

# 좌회전시 조건
right_flag = head_true & (cmatch.turn_type=='left')

# 보행신호시/좌회전시 진입/진출 엣지id 배정
cmatch[['inc_edge_id', 'out_edge_id']] = np.nan
if condition == "보행신호시":
    cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
elif condition == "좌회전시":
    cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]

display(cmatch)

i2 u20 보행신호시


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       177         1         A        8        남        북       179   
1       177         1         B        4        북        남       000   
2       177         2         A        7        북        동       000   
3       177         2         B        3        남        서       179   
4       177         4         A        5        서        북       268   
5       177         4         B        1        동        남       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542809_01  571542811_01     u20      left  
1       180   571542811_02  571542809_01     u20  straight  
2       090   571542811_02  571542107_01     u20      left  
3       270  -571542809_01  571542809_01     u20      left  
4       000  -571542809_01  571542811_01     u20      left  
5       180   571542107_02  571542809_01     u20      left

0
[-360 -270 -181  -92    0   90  179  268  360  450  539  628]
[ 90 179 268 360 450 539 628]
90
571542107_02
[-360 -270 -180  -90    0   90  180  270  360  450  540  630]
[-360 -270 -180  -90]
270
571542809_01


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       177         1         A        8        남        북       179   
1       177         1         B        4        북        남       000   
2       177         2         A        7        북        동       000   
3       177         2         B        3        남        서       179   
4       177         4         A        5        서        북       268   
5       177         4         B        1        동        남       090   

  out_angle      inc_edge_id   out_edge_id node_id turn_type  
0       000              NaN           NaN     u20      left  
1       180              NaN           NaN     u20  straight  
2       090              NaN           NaN     u20      left  
3       270              NaN           NaN     u20      left  
4       000              NaN           NaN     u20      left  
5       180  571542810_01.51  571542810_02     u20      left

In [ ]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    dire = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id

    print(parent_id, condition)

    # match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge_id', 'out_edge_id']] = np.nan
    display(cmatch)

    # 보행신호시/좌회전시 진입/진출방향
    ind = self.dires.index(dire)
    inc_dire_pedes = self.dires[(ind + 2) % len(self.dires)]
    out_dire_pedes = self.dires[(ind - 2) % len(self.dires)]
    inc_dire_right = dire
    out_dire_right = self.dires[(ind + 2) % len(self.dires)]

    if condition == '보행신호시':
        print(inc_dire_pedes, out_dire_pedes)
    else:
        print(inc_dire_right, out_dire_right)

    # 보행신호시/좌회전시 조건
    pedes_exists = (cmatch.inc_dire==inc_dire_pedes) & (cmatch.out_dire==out_dire_pedes)
    right_exists = (cmatch.inc_dire==inc_dire_right) & (cmatch.out_dire==out_dire_right)

    # 보행신호시/좌회전시 진입/진출 엣지id 배정
    ind = self.dires.index(dire)
    if condition == "보행신호시":
        cmatch.loc[pedes_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    elif condition == "좌회전시":
        cmatch.loc[right_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    display(cmatch)

    # 신호없음이동류발생시/보행신호이동류발생시 조건
    all_redsigns = cmatch.move_no == 18
    crosswalk_on = cmatch.move_no == 17

    # 만약 어떤 유턴신호도 배정되지 않았다면
    # 좌회전시 → 보행신호시 → 보행신호이동류발생시 → 신호없음이동류발생시 순으로 진입/진출 엣지id 배정
    uturn_not_assigned = cmatch[['inc_edge_id','out_edge_id']].isna().any(axis=1).all()
    if uturn_not_assigned:
        # 좌회전시
        if right_exists.any():
            cmatch.loc[right_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호시
        elif pedes_exists.any():
            cmatch.loc[pedes_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호이동류(17) 발생시
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on & (cmatch.out_dire!=dire), ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 신호없음이동류(18) 발생시
        elif all_redsigns.any():
            cmatch.loc[all_redsigns & (cmatch.out_dire!=dire), ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    display(cmatch)
cmatches.append(cmatch)


In [ ]:
'''Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.'''